In [ ]:
import os
import pandas as pd
job_id='dj-synhub-extraction-lkbi9fy6zepu8rcjuxqhjwkbld52wgt0-sc2bx1af4k'


df = pd.read_csv(f'../../extractions/{job_id}/result_deduped_semantic.csv')
cols2drop=['title','snippet','word_count','section','segment_norm','segment_hash','num_segments'] # body
cols2rename={"segment":"article_text"}
df.drop(columns=cols2drop,inplace=True)
df.rename(columns=cols2rename,inplace=True)
df

original_index                                        source_name  \
0                   0                                      The Telegraph   
1                   0                                      The Telegraph   
2                   0                                      The Telegraph   
3                   0                                      The Telegraph   
4                   8  AfU Company Information: Mutual Fund Holdings ...   
...               ...                                                ...   
76969           46675                                  walesonline.co.uk   
76970           46675                                  walesonline.co.uk   
76971           46675                                  walesonline.co.uk   
76972           46675                                  walesonline.co.uk   
76973           46676                                  walesonline.co.uk   

                                                    body source_code  \
0      London-based multinational insurance and asset...      ABPTEL   
1      London-based multinational insurance and asset...      ABPTEL   
2      London-based multinational insurance and asset...      ABPTEL   
3      London-based multinational insurance and asset...      ABPTEL   
4      all german mutual funds\n\nshare_name         ...      ACIIBC   
...                                                  ...         ...   
76969  Mr Griffith is the former chief executive and ...    WALESONL   
76970  Mr Griffith is the former chief executive and ...    WALESONL   
76971  Mr Griffith is the former chief executive and ...    WALESONL   
76972  Mr Griffith is the former chief executive and ...    WALESONL   
76973  It is vacating around 70,000 sq ft of space at...    WALESONL   

                                          industry_codes  \
0                             ,i82,i82001,i82002,ifinal,   
1                             ,i82,i82001,i82002,ifinal,   
2                             ,i82,i82001,i82002,ifinal,   
3                             ,i82,i82001,i82002,ifinal,   
4      ,i31,i814,i81502,i8150211,i831,i83101,i83107,i...   
...                                                  ...   
76969                            ,i836,iacc,ibcs,ifinal,   
76970                            ,i836,iacc,ibcs,ifinal,   
76971                            ,i836,iacc,ibcs,ifinal,   
76972                            ,i836,iacc,ibcs,ifinal,   
76973  ,i814,i81402,i81404,i81501,i8150104,i831,ibnk,...   

                                           company_codes  \
0      allanz,bajaal,blfima,hcltec,icplic,paions,pias...   
1      allanz,bajaal,blfima,hcltec,icplic,paions,pias...   
2      allanz,bajaal,blfima,hcltec,icplic,paions,pias...   
3      allanz,bajaal,blfima,hcltec,icplic,paions,pias...   
4      albts,blaman,brbgg,dinvsg,indeia,montpv,smns,u...   
...                                                  ...   
76969           fisgbo,fsrcsl,moilga,ombud,vhskrn,vibidl   
76970           fisgbo,fsrcsl,moilga,ombud,vhskrn,vibidl   
76971           fisgbo,fsrcsl,moilga,ombud,vhskrn,vibidl   
76972           fisgbo,fsrcsl,moilga,ombud,vhskrn,vibidl   
76973  acacq,bredo,ckark,crdffu,dunbst,ltgil,momlas,p...   

                                           subject_codes  \
0      ,c13,c18,c184,cactio,ccat,cpartn,ncat,nfact,nf...   
1      ,c13,c18,c184,cactio,ccat,cpartn,ncat,nfact,nf...   
2      ,c13,c18,c184,cactio,ccat,cpartn,ncat,nfact,nf...   
3      ,c13,c18,c184,cactio,ccat,cpartn,ncat,nfact,nf...   
4               ,c18,c181,cactio,ccat,ncat,nfact,nfcpin,   
...                                                  ...   
76969  ,c18,cactio,ccat,cliqui,grugu,gspo,ncat,nfact,...   
76970  ,c18,cactio,ccat,cliqui,grugu,gspo,ncat,nfact,...   
76971  ,c18,cactio,ccat,cliqui,grugu,gspo,ncat,nfact,...   
76972  ,c18,cactio,ccat,cliqui,grugu,gspo,ncat,nfact,...   
76973                              ,c02,ccat,chqr,coffs,   

          publication_datetime   ingestion_datetime        modific

## Processing results

In [5]:
from factiva.news.taxonomy import Taxonomy

user_key = 'LKbI9fY6ZEPU8RcJUxQHjwKbld52WGt0'
taxonomy=Taxonomy(user_key=user_key)
companies_taxonomy_df= taxonomy.get_category_codes('companies')
companies_mapping = companies_taxonomy_df['description'].to_dict()
companies_mapping = {k.lower(): v for k, v in companies_mapping.items()}

In [6]:
results_df = pd.read_csv(f'../../extractions/{job_id}/classification_results.csv_2025-05-08_20-12-30.csv')
cols_mapping = {'is_co': 'is_about_carve_out',"co_confidence": "carve_out_confidence"}
results_df = results_df.rename(columns=cols_mapping)
results_df['target_company'] = results_df['target_company_code'].map(companies_mapping)
results_df

is_about_carve_out target_company_code  is_relevant  \
0                   False                 pru        False   
1                   False              allanz        False   
2                   False                 NaN        False   
3                   False                 NaN        False   
4                   False                 NaN        False   
...                   ...                 ...          ...   
76969               False                 NaN         True   
76970               False                 NaN        False   
76971               False                 NaN        False   
76972               False                 NaN        False   
76973               False                 NaN        False   

                                         short_reasoning  \
0      The article describes Prudential PLC's strateg...   
1      The article discusses Allianz's strategic move...   
2      The article discusses partnerships and growth ...   
3      The article discusses partnerships and market ...   
4      The article lists mutual fund holdings in Aalb...   
...                                                  ...   
76969  The article discusses the collapse of a financ...   
76970  The article discusses a collapsed financial se...   
76971  The article discusses the collapse of a financ...   
76972  The article reports on Optima Worldwide Group ...   
76973  The article primarily discusses MotoNovo's fin...   

                                  original_company_codes  \
0      allanz,bajaal,blfima,hcltec,icplic,paions,pias...   
1      allanz,bajaal,blfima,hcltec,icplic,paions,pias...   
2      allanz,bajaal,blfima,hcltec,icplic,paions,pias...   
3      allanz,bajaal,blfima,hcltec,icplic,paions,pias...   
4      albts,blaman,brbgg,dinvsg,indeia,montpv,smns,u...   
...                                                  ...   
76969           fisgbo,fsrcsl,moilga,ombud,vhskrn,vibidl   
76970           fisgbo,fsrcsl,moilga,ombud,vhskrn,vibidl   
76971           fisgbo,fsrcsl,moilga,ombud,vhskrn,vibidl   
76972           fisgbo,fsrcsl,moilga,ombud,vhskrn,vibidl   
76973  acacq,bredo,ckark,crdffu,dunbst,ltgil,momlas,p...   

                                      original_companies  index  \
0      Allianz SE,Bajaj Auto Limited,Bloomberg LP,HCL...      0   
1      Allianz SE,Bajaj Auto Limited,Bloomberg LP,HCL...      1   
2      Allianz SE,Bajaj Auto Limited,Bloomberg LP,HCL...      2   
3      Allianz SE,Bajaj Auto Limited,Bloomberg LP,HCL...      3   
4      Aalberts N.V.,BlackRock Inc,Joh. Berenberg, Go...      4   
...                                                  ...    ...   
76969  Optima Worldwide Group PLC,Financial Services ...  76969   
76970  Optima Worldwide Group PLC,Financial Services ...  76970   
76971  Optima Worldwide Group PLC,Financial Services ...  76971   
76972  Optima Worldwide Group PLC,Financial Services ...  76972   
76973  Aldermore Group PLC,Brewin Dolphin Holdings PL...  76973   

       target_company  
0      Prudential PLC  
1          Allianz SE  
2                 NaN  
3                 NaN  
4                 NaN  
...               ...  
76969             NaN  
76970             NaN  
76971             NaN  
76972             NaN  
76973             NaN  

[76974 rows x 8 columns]

In [7]:
results_df[results_df.is_about_carve_out == 1]

is_about_carve_out target_company_code  is_relevant  \
572                  True                barc         True   
576                  True              glopmt         True   
577                  True              glopmt         True   
628                  True              afsvcg         True   
638                  True              alibab         True   
...                   ...                 ...          ...   
76898                True                smin         True   
76902                True               rbsct         True   
76926                True                 pru         True   
76927                True                 pru         True   
76953                True               thwat         True   

                                         short_reasoning  \
572    Barclays is creating a standalone payments bus...   
576    Global Payments announced agreements to divest...   
577    Global Payments Inc. is divesting its Issuer S...   
628    Aeon Financial Service Co., Ltd. has appointed...   
638    The article discusses Ant Group's restructurin...   
...                                                  ...   
76898  Smiths Group has announced plans to sell or de...   
76902  The article highlights that the UK government ...   
76926  Prudential is signaling a strategic refocus to...   
76927  Prudential previously demerged its UK and Euro...   
76953  The article discusses Thames Water's potential...   

                                  original_company_codes  \
572    aencre,afsvcg,alibab,allpau,altosv,amexpr,amzc...   
576    aencre,afsvcg,alibab,allpau,altosv,amexpr,amzc...   
577    aencre,afsvcg,alibab,allpau,altosv,amexpr,amzc...   
628    aencre,afsvcg,alibab,allpau,altosv,amexpr,amzc...   
638    aencre,afsvcg,alibab,allpau,altosv,amexpr,amzc...   
...                                                  ...   
76898  alvmar,artboe,athmgl,bdgrln,blfima,bp,coca,cst...   
76902                        barc,hksbc,mbkplc,rbsct,tsb   
76926                              icbkbo,piasmc,pru,ubs   
76927                              icbkbo,piasmc,pru,ubs   
76953      mcqbnk,octocp,oenhlm,ofwat,sueze,thawul,thwat   

                                      original_companies  index  \
572    Aeon Financial Service Co., Ltd.,Ant Group Com...    572   
576    Aeon Financial Service Co., Ltd.,Ant Group Com...    576   
577    Aeon Financial Service Co., Ltd.,Ant Group Com...    577   
628    Aeon Financial Service Co., Ltd.,Ant Group Com...    628   
638    Aeon Financial Service Co., Ltd.,Ant Group Com...    638   
...                                                  ...    ...   
76898  Alvarez & Marsal Inc,Anheuser-Busch InBev SA/N...  76898   
76902  Barclays PLC,HSBC Holdings PLC,Metro Bank Hold...  76902   
76926  ICICI Bank Ltd,ICICI Prudential Asset Manageme...  76926   
76927  ICICI Bank Ltd,ICICI Prudential Asset Manageme...  76927   
76953  Macquarie Group Limited,Octopus Capital Limite...  76953   

                  target_company  
572                 Barclays PLC  
576         Global Payments Inc.  
577         Global Payments Inc.  
628    Ant Group Company Limited  
638    Alibaba Group Holding Ltd  
...                          ...  
76898           Smiths Group PLC  
76902          NatWest Group PLC  
76926             Prudential PLC  
76927             Prudential PLC  
76953           Thames Water Ltd  

[2723 rows x 8 columns]

In [9]:
def process_results(orig_df, preds_df, output_dir=f'../../extractions/{job_id}/'):
    
    res_df = orig_df.merge(preds_df, how='left', left_index=True, right_index=True)
    
    res_df.to_excel(os.path.join(output_dir, 'final_analysis_results.xlsx'), index=False)
    print(f"Results saved to {os.path.join(output_dir, 'final_analysis_results.xlsx')}")
    
    filtered_results = res_df[res_df.is_about_carve_out].copy()
    filtered_results.to_excel(
        os.path.join(output_dir, 'filtered_as_carve_out_results.xlsx'), index=False
    )
        
    return res_df, filtered_results

In [10]:
preds_df,filtered_results = process_results(df, results_df)
filtered_results

Results saved to ../../extractions/dj-synhub-extraction-lkbi9fy6zepu8rcjuxqhjwkbld52wgt0-sc2bx1af4k/final_analysis_results.xlsx


original_index                          source_name  \
572              3748  Acquisdata Global Industry SnapShot   
576              3748  Acquisdata Global Industry SnapShot   
577              3748  Acquisdata Global Industry SnapShot   
628              3748  Acquisdata Global Industry SnapShot   
638              3748  Acquisdata Global Industry SnapShot   
...               ...                                  ...   
76898           46662                       thetimes.co.uk   
76902           46664                       thetimes.co.uk   
76926           46667                       thetimes.co.uk   
76927           46667                       thetimes.co.uk   
76953           46671                       thetimes.co.uk   

                                                    body source_code  \
572    Forbes – Plaid Raises $575 Million In Funding ...      ACQIND   
576    Forbes – Plaid Raises $575 Million In Funding ...      ACQIND   
577    Forbes – Plaid Raises $575 Million In Funding ...      ACQIND   
628    Forbes – Plaid Raises $575 Million In Funding ...      ACQIND   
638    Forbes – Plaid Raises $575 Million In Funding ...      ACQIND   
...                                                  ...         ...   
76898  Elliott Management, the New York-based hedge f...      TIMEUK   
76902  The FTSE 100 lender, which is led by Paul Thwa...      TIMEUK   
76926  The FTSE 100-listed insurance group has been w...      TIMEUK   
76927  The FTSE 100-listed insurance group has been w...      TIMEUK   
76953  Kraken Technologies, an arm of Octopus Energy,...      TIMEUK   

                                          industry_codes  \
572    ,i3441,i831,i83107,iblock,ifinal,ifmsoft,iinv,...   
576    ,i3441,i831,i83107,iblock,ifinal,ifmsoft,iinv,...   
577    ,i3441,i831,i83107,iblock,ifinal,ifmsoft,iinv,...   
628    ,i3441,i831,i83107,iblock,ifinal,ifmsoft,iinv,...   
638    ,i3441,i831,i83107,iblock,ifinal,ifmsoft,iinv,...   
...                                                  ...   
76898                ,i81502,ialtinv,ifinal,ihedge,iinv,   
76902                          ,i814,i81402,ibnk,ifinal,   
76926        ,i82,i82002,i831,i83107,i83108,ifinal,iinv,   
76927        ,i82,i82002,i831,i83107,i83108,ifinal,iinv,   
76953  ,i1,i16,i17,i81502,ialtinv,ifinal,ihedge,iinv,...   

                                           company_codes  \
572    aencre,afsvcg,alibab,allpau,altosv,amexpr,amzc...   
576    aencre,afsvcg,alibab,allpau,altosv,amexpr,amzc...   
577    aencre,afsvcg,alibab,allpau,altosv,amexpr,amzc...   
628    aencre,afsvcg,alibab,allpau,altosv,amexpr,amzc...   
638    aencre,afsvcg,alibab,allpau,altosv,amexpr,amzc...   
...                                                  ...   
76898  alvmar,artboe,athmgl,bdgrln,blfima,bp,coca,cst...   
76902                        barc,hksbc,mbkplc,rbsct,tsb   
76926                              icbkbo,piasmc,pru,ubs   
76927                              icbkbo,piasmc,pru,ubs   
76953      mcqbnk,octocp,oenhlm,ofwat,sueze,thawul,thwat   

                                           subject_codes  \
572    ,c18,c181,cacqu,cactio,ccat,cdom,ciprof,gcat,g...   
576    ,c18,c181,cacqu,cactio,ccat,cdom,ciprof,gcat,g...   
577    ,c18,c181,cacqu,cactio,ccat,cdom,ciprof,gcat,g...   
628    ,c18,c181,cacqu,cactio,ccat,cdom,ciprof,gcat,g...   
638    ,c18,c181,cacqu,cactio,ccat,cdom,ciprof,gcat,g...   
...                                                  ...   
76898  ,c18,c181,c41,cactio,cactsh,ccat,ccpgvn,cesg,n...   
76902  ,c15,c151,c18,c181,cactio,ccat,ncat,nfact,nfcpin,   
76926  ,c02,c14,c17,c171,c1711,c18,c181,cactio,ccat,c...   
76927  ,c02,c14,c17,c171,c1711,c18,c181,cactio,ccat,c...   
76953      ,c18,c181,c183,cactio,ccat,ncat,nfact,nfcpin,   

          publication_datetime   ingestion_datetime        modification_date  \
572        2025-04-21 00:00:00  2025-04-25 10:06:58  2025-04-26 07:33:20.526   
576        2025-04-21 00:00:00  2025-04-25 10:06:58  2025-04-26 07:33:20.5

In [106]:
filtered_targets_df = filtered_results[['modification_date','target_company_code','target_company']].rename(columns={'modification_date':'article_date'}).sort_values(by='article_date', ascending=False).drop_duplicates(subset=['target_company_code'], keep='first')#.reset_index(drop=True)

# Manual fix for some empty target companies - work on that in next iter
filtered_targets_df.loc[20398,'target_company'] = 'Swedbank AB'
filtered_targets_df.loc[20398,'target_company_code'] = 'spargp'

filtered_targets_df.dropna(subset=['target_company'], inplace=True)
filtered_targets_df.reset_index(drop=True, inplace=True)
filtered_targets_df

article_date target_company_code  \
0    2025-05-07 07:30:46.466                hsbk   
1    2025-05-07 07:30:33.985              bncstd   
2    2025-05-07 07:30:32.306                yulc   
3    2025-05-07 07:28:39.275               wrdhv   
4    2025-05-07 07:28:00.622              amexpr   
..                       ...                 ...   
688  2024-12-14 07:17:20.672              fsautt   
689  2024-12-14 07:17:20.672              kccgjd   
690  2024-12-14 07:17:20.672              resinp   
691  2024-12-14 07:16:39.924                bupa   
692  2024-12-14 07:12:30.320              jobgse   

                                      target_company  
0                                 Hang Seng Bank Ltd  
1                                 Banco Santander SA  
2                                      Synthomer PLC  
3                                      Wereldhave NV  
4                                American Express Co  
..                                               ...  
688                      Financial Conduct Authority  
689  Ecofin U.S. Renewables Infrastructure Trust PLC  
690                             Nativo Resources PLC  
691         British United Provident Association Ltd  
692                                      JSE Limited  

[693 rows x 3 columns]

## Quick clf - is company relevant to business request? (is it European?)

In [53]:
from pydantic import BaseModel,Field
from typing import List, Any, Dict

class CompanyRelevancy(BaseModel):
    target_company: str = Field(description="Name of the target company, same as in the provided example")
    is_relevant: bool = Field(description="Is the company `relevant` to the conditions of business request? (Is it European or be interested in carving-out smth it owns in Europe or EEAA?)")
    confidence: float = Field(description="Confidence score of the model that the company is relevant to the conditions of business request")

 
PROMPT = """Given name of target company, estimate if it is related to business request. 
Business request is: 
* Geography (Europe) - meaning that the company is located in Europe or is interested in carving-out its European market

* Deal technique (Divestment)
* Sector (Financial services)

Company name: {target_company}
"""


from llm_utils.factory import construct_llm, LLMChainFactory
llm = construct_llm(model_name='gpt-4.1', temperature=0.1)
factory = LLMChainFactory(model_name='gpt-4.1', temperature=0.1)
# simple_chain = factory.build_simple_prompt(llm, template=template)
so_chain = factory._runnable_with_structured(template=PROMPT, response_schemas=CompanyRelevancy, llm=llm)


def df_to_prompt_inputs(df: pd.DataFrame) -> List[Dict[str, Any]]:
    """
    Convert a DataFrame with columns ['index','target_company']
    into a list of dicts compatible with your prompt template keys:
    """
    return df['target_company'].reset_index().to_dict(orient='records')


def chunk_list(items: List[Any], batch_size: int) -> List[List[Any]]:
    """
    Split a list into sublists (batches) of max length `batch_size`.
    """
    return [items[i:i + batch_size] for i in range(0, len(items), batch_size)]

chunked_list = chunk_list(df_to_prompt_inputs(filtered_targets_df), 30)

In [47]:
from langchain.callbacks import get_openai_callback
from tqdm.auto import tqdm

def simple_batch_with_usage(batch, chain):
    # Wrap the call in the OpenAI callback context
    with get_openai_callback() as cb:
        results = chain.batch(batch)

    return results, cb

simple_batch_with_usage(chunked_list[0], so_chain)

INFO:httpx:HTTP Request: POST https://openai-nc-east-us-2.openai.azure.com/openai/deployments/gpt-4.1/chat/completions?api-version=2025-03-01-preview "HTTP/1.1 200 OK"
INFO:httpx:HTTP Request: POST https://openai-nc-east-us-2.openai.azure.com/openai/deployments/gpt-4.1/chat/completions?api-version=2025-03-01-preview "HTTP/1.1 200 OK"
INFO:httpx:HTTP Request: POST https://openai-nc-east-us-2.openai.azure.com/openai/deployments/gpt-4.1/chat/completions?api-version=2025-03-01-preview "HTTP/1.1 200 OK"
INFO:httpx:HTTP Request: POST https://openai-nc-east-us-2.openai.azure.com/openai/deployments/gpt-4.1/chat/completions?api-version=2025-03-01-preview "HTTP/1.1 200 OK"
INFO:httpx:HTTP Request: POST https://openai-nc-east-us-2.openai.azure.com/openai/deployments/gpt-4.1/chat/completions?api-version=2025-03-01-preview "HTTP/1.1 200 OK"
INFO:httpx:HTTP Request: POST https://openai-nc-east-us-2.openai.azure.com/openai/deployments/gpt-4.1/chat/completions?api-version=2025-03-01-preview "HTTP/1.1 

([CompanyRelevancy(target_company='Hang Seng Bank Ltd', is_relevant=False, confidence=0.15),
  CompanyRelevancy(target_company='Banco Santander SA', is_relevant=True, confidence=0.98),
  CompanyRelevancy(target_company='Synthomer PLC', is_relevant=False, confidence=0.2),
  CompanyRelevancy(target_company='Wereldhave NV', is_relevant=True, confidence=0.9),
  CompanyRelevancy(target_company='American Express Co', is_relevant=True, confidence=0.6),
  CompanyRelevancy(target_company='American Express Banking Corporation', is_relevant=False, confidence=0.2),
  CompanyRelevancy(target_company='Globetel European Limited', is_relevant=True, confidence=0.85),
  CompanyRelevancy(target_company='Raiffeisen Bank International AG', is_relevant=True, confidence=0.98),
  CompanyRelevancy(target_company='Oddo BHF AG', is_relevant=True, confidence=0.95),
  CompanyRelevancy(target_company='Ed Broking Group Limited', is_relevant=True, confidence=0.85),
  CompanyRelevancy(target_company='ReNew Energy Glob

In [56]:
import time
from typing import List, Dict, Any
from pathlib import Path
from datetime import datetime
import pandas as pd
from tqdm.auto import tqdm

def process_and_save(
    chunks: List[List[Dict[str, Any]]],
    chain,
    partial_every: int = 10,
    partial_dir: str = "partials",
    final_path: str = "classification_results.csv",
    max_retries: int = 5,
    initial_delay: float = 5.0,
) -> pd.DataFrame:
    """
    Iterate over each chunk of inputs, run the chain with retry logic, and save results:
      - Shows a progress bar over chunks.
      - Retries on failure with exponential backoff.
      - Saves partial CSV after every `partial_every` chunks into `partial_dir`.
      - Saves the final combined results as `final_path`.
      - Uses company codes from input chunks instead of LLM responses.
    
    Args:
        chunks: List of batches of prompt-input dicts.
        chain: RunnableSequence with .batch().
        partial_every: Save a partial CSV every N chunks.
        partial_dir: Directory to save partial CSVs.
        final_path: Filepath for the final CSV.
        max_retries: How many times to retry a failed chunk.
        initial_delay: Base delay (in seconds) for exponential backoff.
    
    Returns:
        DataFrame of all successful results.
    """
    partial_dir = f"{partial_dir}_{datetime.now().strftime('%Y-%m-%d_%H-%M-%S')}"
    Path(partial_dir).mkdir(parents=True, exist_ok=True)
    all_records = []
    failed_chunks = []

    for idx, batch in enumerate(tqdm(chunks, desc="Processing chunks")):
        # Retry logic per chunk
        for attempt in range(1, max_retries + 1):
            try:
                assessments = chain.batch(batch)
                break
            except Exception as e:
                print(f"[Chunk {idx}][Attempt {attempt}] Error: {e}")
                if attempt < max_retries:
                    delay = initial_delay * (2 ** (attempt - 1))
                    print(f"  Retrying in {delay:.1f}s...")
                    time.sleep(delay)
                else:
                    print(f"  Chunk {idx} failed after {max_retries} attempts, skipping.")
                    failed_chunks.append(idx)
        else:
            continue

        records = []
        for i, assessment in enumerate(assessments):
            record = assessment.model_dump()
            
            record['original_target_company'] = batch[i].get('target_company', '')
            record['index'] = batch[i].get('index', None)

            records.append(record)
            
        all_records.extend(records)

        # Save partials
        if (idx + 1) % partial_every == 0:
            df_partial = pd.DataFrame(all_records)
            df_partial.to_csv(Path(partial_dir) / f"partial_{idx+1}.csv", index=False)
            print(f"Saved partial results to {partial_dir}/partial_{idx+1}.csv")
        time.sleep(5)
    
    # Save final results
    df_final = pd.DataFrame(all_records)
    final_file = Path(f"{final_path}_{datetime.now().strftime('%Y-%m-%d_%H-%M-%S')}.csv")
    final_file.parent.mkdir(parents=True, exist_ok=True)
    df_final.to_csv(final_file, index=False)
    print(f"Saved final results to {final_file}")

    if failed_chunks:
        print(f"Warning: the following chunks failed and were skipped: {failed_chunks}")
    
    return df_final

In [57]:
df_results = process_and_save(
    chunked_list[:],
    so_chain,
    partial_every=10,
    partial_dir=f"../../extractions/{job_id}/partial_outputs_filtering",
    final_path=f"../../extractions/{job_id}/final_filtering_results.csv",
    max_retries=4,
    initial_delay=5.0)

Processing chunks:   0%|          | 0/24 [00:00<?, ?it/s]

INFO:httpx:HTTP Request: POST https://openai-nc-east-us-2.openai.azure.com/openai/deployments/gpt-4.1/chat/completions?api-version=2025-03-01-preview "HTTP/1.1 200 OK"
INFO:httpx:HTTP Request: POST https://openai-nc-east-us-2.openai.azure.com/openai/deployments/gpt-4.1/chat/completions?api-version=2025-03-01-preview "HTTP/1.1 200 OK"
INFO:httpx:HTTP Request: POST https://openai-nc-east-us-2.openai.azure.com/openai/deployments/gpt-4.1/chat/completions?api-version=2025-03-01-preview "HTTP/1.1 200 OK"
INFO:httpx:HTTP Request: POST https://openai-nc-east-us-2.openai.azure.com/openai/deployments/gpt-4.1/chat/completions?api-version=2025-03-01-preview "HTTP/1.1 200 OK"
INFO:httpx:HTTP Request: POST https://openai-nc-east-us-2.openai.azure.com/openai/deployments/gpt-4.1/chat/completions?api-version=2025-03-01-preview "HTTP/1.1 200 OK"
INFO:httpx:HTTP Request: POST https://openai-nc-east-us-2.openai.azure.com/openai/deployments/gpt-4.1/chat/completions?api-version=2025-03-01-preview "HTTP/1.1 

Saved partial results to ../../extractions/dj-synhub-extraction-lkbi9fy6zepu8rcjuxqhjwkbld52wgt0-sc2bx1af4k/partial_outputs_filtering_2025-05-08_21-54-01/partial_10.csv


INFO:httpx:HTTP Request: POST https://openai-nc-east-us-2.openai.azure.com/openai/deployments/gpt-4.1/chat/completions?api-version=2025-03-01-preview "HTTP/1.1 200 OK"
INFO:httpx:HTTP Request: POST https://openai-nc-east-us-2.openai.azure.com/openai/deployments/gpt-4.1/chat/completions?api-version=2025-03-01-preview "HTTP/1.1 200 OK"
INFO:httpx:HTTP Request: POST https://openai-nc-east-us-2.openai.azure.com/openai/deployments/gpt-4.1/chat/completions?api-version=2025-03-01-preview "HTTP/1.1 200 OK"
INFO:httpx:HTTP Request: POST https://openai-nc-east-us-2.openai.azure.com/openai/deployments/gpt-4.1/chat/completions?api-version=2025-03-01-preview "HTTP/1.1 200 OK"
INFO:httpx:HTTP Request: POST https://openai-nc-east-us-2.openai.azure.com/openai/deployments/gpt-4.1/chat/completions?api-version=2025-03-01-preview "HTTP/1.1 200 OK"
INFO:httpx:HTTP Request: POST https://openai-nc-east-us-2.openai.azure.com/openai/deployments/gpt-4.1/chat/completions?api-version=2025-03-01-preview "HTTP/1.1 

Saved partial results to ../../extractions/dj-synhub-extraction-lkbi9fy6zepu8rcjuxqhjwkbld52wgt0-sc2bx1af4k/partial_outputs_filtering_2025-05-08_21-54-01/partial_20.csv


INFO:httpx:HTTP Request: POST https://openai-nc-east-us-2.openai.azure.com/openai/deployments/gpt-4.1/chat/completions?api-version=2025-03-01-preview "HTTP/1.1 200 OK"
INFO:httpx:HTTP Request: POST https://openai-nc-east-us-2.openai.azure.com/openai/deployments/gpt-4.1/chat/completions?api-version=2025-03-01-preview "HTTP/1.1 200 OK"
INFO:httpx:HTTP Request: POST https://openai-nc-east-us-2.openai.azure.com/openai/deployments/gpt-4.1/chat/completions?api-version=2025-03-01-preview "HTTP/1.1 200 OK"
INFO:httpx:HTTP Request: POST https://openai-nc-east-us-2.openai.azure.com/openai/deployments/gpt-4.1/chat/completions?api-version=2025-03-01-preview "HTTP/1.1 200 OK"
INFO:httpx:HTTP Request: POST https://openai-nc-east-us-2.openai.azure.com/openai/deployments/gpt-4.1/chat/completions?api-version=2025-03-01-preview "HTTP/1.1 200 OK"
INFO:httpx:HTTP Request: POST https://openai-nc-east-us-2.openai.azure.com/openai/deployments/gpt-4.1/chat/completions?api-version=2025-03-01-preview "HTTP/1.1 

Saved final results to ../../extractions/dj-synhub-extraction-lkbi9fy6zepu8rcjuxqhjwkbld52wgt0-sc2bx1af4k/final_filtering_results.csv_2025-05-08_21-56-41.csv


In [107]:
final_targets_df = filtered_targets_df.merge(df_results.loc[:,df_results.columns!='target_company'], how='left', left_index=True, right_index=True).copy()
final_targets_df

article_date target_company_code  \
0    2025-05-07 07:30:46.466                hsbk   
1    2025-05-07 07:30:33.985              bncstd   
2    2025-05-07 07:30:32.306                yulc   
3    2025-05-07 07:28:39.275               wrdhv   
4    2025-05-07 07:28:00.622              amexpr   
..                       ...                 ...   
688  2024-12-14 07:17:20.672              fsautt   
689  2024-12-14 07:17:20.672              kccgjd   
690  2024-12-14 07:17:20.672              resinp   
691  2024-12-14 07:16:39.924                bupa   
692  2024-12-14 07:12:30.320              jobgse   

                                      target_company  is_relevant  confidence  \
0                                 Hang Seng Bank Ltd        False        0.10   
1                                 Banco Santander SA         True        0.99   
2                                      Synthomer PLC        False        0.10   
3                                      Wereldhave NV         True        0.90   
4                                American Express Co         True        0.80   
..                                               ...          ...         ...   
688                      Financial Conduct Authority        False        0.99   
689  Ecofin U.S. Renewables Infrastructure Trust PLC        False        0.10   
690                             Nativo Resources PLC        False        0.15   
691         British United Provident Association Ltd         True        0.95   
692                                      JSE Limited        False        0.95   

                             original_target_company  index  
0                                 Hang Seng Bank Ltd      0  
1                                 Banco Santander SA      1  
2                                      Synthomer PLC      2  
3                                      Wereldhave NV      3  
4                                American Express Co      4  
..                                               ...    ...  
688                      Financial Conduct Authority    688  
689  Ecofin U.S. Renewables Infrastructure Trust PLC    689  
690                             Nativo Resources PLC    690  
691         British United Provident Association Ltd    691  
692                                      JSE Limited    692  

[693 rows x 7 columns]

In [108]:
final_targets_df.drop(columns=['index'], inplace=True)
final_targets_df.sort_values(by=['is_relevant','confidence','article_date'], ascending=False, inplace=True)

final_targets_df

article_date target_company_code               target_company  \
1    2025-05-07 07:30:33.985              bncstd           Banco Santander SA   
79   2025-04-30 07:22:57.883                deut             Deutsche Bank AG   
115  2025-04-23 07:37:55.046                 tsb     Lloyds Banking Group PLC   
151  2025-04-17 07:25:00.727                  sg             Societe Generale   
203  2025-04-12 07:35:55.155              allanz                   Allianz SE   
..                       ...                 ...                          ...   
359  2025-03-13 07:39:26.138              kbfing      KB Financial Group Inc.   
381  2025-03-08 07:23:31.938              svenih  Seven & I Holdings Co. Ltd.   
424  2025-02-27 07:36:26.850              bnmiss                 Cadence Bank   
602  2025-01-15 07:20:34.967                 edf     Electricite de France SA   
666  2024-12-19 07:23:52.852              untinc                 Kemper Corp.   

     is_relevant  confidence      original_target_company  
1           True        0.99           Banco Santander SA  
79          True        0.99             Deutsche Bank AG  
115         True        0.99     Lloyds Banking Group PLC  
151         True        0.99             Societe Generale  
203         True        0.99                   Allianz SE  
..           ...         ...                          ...  
359        False        0.05      KB Financial Group Inc.  
381        False        0.05  Seven & I Holdings Co. Ltd.  
424        False        0.05                 Cadence Bank  
602        False        0.05     Electricite de France SA  
666        False        0.05                 Kemper Corp.  

[693 rows x 6 columns]

In [109]:
final_targets_df[['article_date','target_company_code','target_company','is_relevant']].to_excel(os.path.join(f'../../extractions/{job_id}', 'filtered_targets.xlsx'), index=False)

## Adding summary output

In [ ]:
from pydantic import BaseModel, Field
class CarveOutSummary(BaseModel):
    target_company: str = Field(description="Name of the target company, same as in the provided example")
    group: str = Field(description="Name of the financial group")
    group_hq: str = Field(description="Base country of the financial group HQ, i.e. UK, US, FI, NL, etc.")
    vertical: str = Field(description="Sector of the financial group, i.e. Banking, Insurance, Data, etc.")
    potential_disposal: str = Field(description="Potential subdivision to be disposed of, i.e. UK business, Insurance Arm, IP business, etc")
    disposal_company_name: str = Field(description="Name of the company to be disposed of, i.e. Swedbank AB, Nordea Bank AB, etc.")
    article_quote: str = Field(description="Quote from the article that supports the conclusion")